# Notebook 7: Twisst analyses

In [1]:
# conda install toytree -c eaton-lab
# conda install ipyrad -c ipyrad


In [2]:
import pandas as pd
import numpy as np
import ipyparallel as ipp
import ipyrad.analysis as ipa
import toyplot
import toytree

In [3]:
assert int(toytree.__version__.split(".")[-1]) > 20, "update toytree to v.0.1.21"

### Connect to parallel client

In [7]:
ipyclient = ipp.Client(cluster_id="alternate")

### Group samples into dictionaries

In [8]:
# which samples are in which clade
fullmap = {
    "virg" : ["TXWV2", "SCCU3", "LALC2", "FLSF33", "FLBA140"],
    "sagr" : ["CUCA4", "CUMM5", "CUSV6", "CUVN10"],
    "fusi" : ["TXGR3", "TXMD3", "MXED8", "MXGT4"],
    "gemi" : ["FLSF54", "FLSF54", "FLWO6", "FLCK18", "FLAB109"],
    "bran" : ["BJSB3", "BJSL25", "BJSL25", "BJVL19", "BJVL19"],
    "oleo" : ["BZBB1", "CRL0001", "CRL0030", "MXSA3017"],
    "mini" : ["FLCK216", "FLMO62", "FLSA185", "FLSF47"],
    
    # outgroups
    "reds" : ["NI", "HE"],
    "whit" : ["AR", "EN", "DO", "DU", "reference"],
    "gold" : ["CH"],
    
    # geographic subsampling
    "fusi-n": ["TXGR3", "TXMD3"],
    "fusi-s": ["MXED8", "MXGT4"],
    "virg-n": [],
    "virg-s": [],
}

# combined groups
fullmap["outg"] = fullmap["reds"] + fullmap["whit"] + fullmap["gold"]
fullmap["flor"] = fullmap["gemi"] + fullmap["virg"] + fullmap["mini"]

## Calculate tree weights tables

### (bran, (virg, (fusi, fusi)));  
Where does fusiformis show greatest gene flow with virginiana (Maybe at a gene involved in frost tolerance?)

In [9]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("virg", "bran", "fusi-n", "fusi-s")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# dictionary to reference results
weights = {}

# iterate over scaffolds
for scaffold in range(12):
    data = "../analysis-treeslider/ts-sc{}-wi100000-sl20000.tree_table.csv".format(scaffold)
    name = "scaf-{}-vbff".format(scaffold)
    
    # init analysis object
    tw = ipa.twisst(
        name=name,
        workdir="../analysis-twisst",
        data=data,
        imap=imap,
        minmap=minmap,
        ipyclient=ipyclient,
    )
    
    # calculate tree weights    
    tw.run(ipyclient, force=True)
    
    # store object in dictionary
    weights[tw.name] = tw

[####################] 100% 0:00:36 | calculating tree weights | scaf-0-vbff 
[####################] 100% 0:01:12 | calculating tree weights | scaf-1-vbff 
[####################] 100% 0:00:32 | calculating tree weights | scaf-2-vbff 
[####################] 100% 0:00:21 | calculating tree weights | scaf-3-vbff 
[####################] 100% 0:00:38 | calculating tree weights | scaf-4-vbff 
[####################] 100% 0:00:31 | calculating tree weights | scaf-5-vbff 
[####################] 100% 0:00:25 | calculating tree weights | scaf-6-vbff 
[####################] 100% 0:00:40 | calculating tree weights | scaf-7-vbff 
[####################] 100% 0:00:27 | calculating tree weights | scaf-8-vbff 
[####################] 100% 0:00:25 | calculating tree weights | scaf-9-vbff 
[####################] 100% 0:00:24 | calculating tree weights | scaf-10-vbff 
[####################] 100% 0:00:20 | calculating tree weights | scaf-11-vbff 


### (outgroup, (oleo, (fusi, bran));

In this test we expect that fusiformis and brandegeei should be equally related to oleoides, and thus it should be fairly random along the genome where a subtree not matching the species tree appears. However, we know that fusiformis and brandegeei have exchanged gene flow, and this should be apparent as isolated regions where (ou,b|ol,f) is more common. 

In [ ]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("whit", "bran", "fusi-s", "oleo")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# dictionary to reference results
weights = {}

# iterate over scaffolds
for scaffold in range(12):
    data = "../analysis-treeslider/ts-sc{}-wi100000-sl20000.tree_table.csv".format(scaffold)
    name = "scaf-{}-obfo".format(scaffold)
    
    # init analysis object
    tw = ipa.twisst(
        name=name,
        workdir="../analysis-twisst",
        data=data,
        imap=imap,
        minmap=minmap,
        ipyclient=ipyclient,
    )
    
    # calculate tree weights    
    tw.run(ipyclient, force=True)
    
    # store object in dictionary
    weights[tw.name] = tw

[####################] 100% 0:00:44 | calculating tree weights | scaf-0-obfo 
[####################] 100% 0:01:29 | calculating tree weights | scaf-1-obfo 
[####################] 100% 0:00:41 | calculating tree weights | scaf-2-obfo 
[####################] 100% 0:00:31 | calculating tree weights | scaf-3-obfo 
[####################] 100% 0:00:50 | calculating tree weights | scaf-4-obfo 
[####################] 100% 0:00:47 | calculating tree weights | scaf-5-obfo 
[####################] 100% 0:00:42 | calculating tree weights | scaf-6-obfo 
[####################] 100% 0:00:56 | calculating tree weights | scaf-7-obfo 
[######              ]  31% 0:00:12 | calculating tree weights | scaf-8-obfo 

### (outgroup, (virg, (mini, gemi));

In this test we expect that virginiana should be equally related to geminata and minima if they are truly sister. However, all three have likely exchanged genes, and virginiana has exchanged genes with other taxa outside of Florida, so it is unclear what to expect. 

In [ ]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("whit", "gemi", "mini", "virg")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# dictionary to reference results
weights = {}

# iterate over scaffolds
for scaffold in range(13):
    data = "../analysis-treeslider/ts-sc{}-wi100000-sl20000.tree_table.csv".format(scaffold)
    name = "scaf-{}-ogmv".format(scaffold)
    
    # init analysis object
    tw = ipa.twisst(
        name=name,
        workdir="../analysis-twisst",
        data=data,
        imap=imap,
        minmap=minmap,
        ipyclient=ipyclient,
    )
    
    # calculate tree weights    
    tw.run(ipyclient, force=True)
    
    # store object in dictionary
    weights[tw.name] = tw

## Plot tree weights on chromosomes

In [9]:
tw = weights["scaf-2-vbff"]
tw.tree_weights.head()

minmap nnodes  abcd  acbd  adbc  unk subtree  fabcd  facbd  fadbc  uabcd  \
0   False    NaN   NaN   NaN   NaN  NaN     NaN    NaN    NaN    NaN    NaN   
1   False    NaN   NaN   NaN   NaN  NaN     NaN    NaN    NaN    NaN    NaN   
2   False    NaN   NaN   NaN   NaN  NaN     NaN    NaN    NaN    NaN    NaN   
3   False    NaN   NaN   NaN   NaN  NaN     NaN    NaN    NaN    NaN    NaN   
4   False    NaN   NaN   NaN   NaN  NaN     NaN    NaN    NaN    NaN    NaN   

   uacbd  uadbc  uunk  
0    NaN    NaN   NaN  
1    NaN    NaN   NaN  
2    NaN    NaN   NaN  
3    NaN    NaN   NaN  
4    NaN    NaN   NaN

In [184]:
from ipyrad.analysis.twiist import *


In [322]:
def calculate_weights(imap, subtree):

    # get a generator of unique nkey samples: e.g., quartets 
    tips = sorted(subtree.get_tip_labels(), key=lambda x: x.rsplit("-", 1)[0])
    groups = itertools.groupby(tips, lambda x: x.rsplit("-", 1)[0])
    quarts = itertools.product(*(set(j) for (i, j) in groups))
    
    # record results
    arr = np.zeros(4, dtype=int)
    
    # prune tree and measure topo dists
    for idx, quart in enumerate(quarts):
        
        # get pruned tree
        droptips = set(subtree.get_tip_labels()) - set(quart)
        dtree = subtree.drop_tips(droptips)
                
        # get treenodes of pruned tips always in alphanumeric order of imaps
        tips = sorted(dtree.get_tip_labels())
        nodes = [dtree.treenode.search_nodes(name=i)[0] for i in tips]
        
        # get splits in the tree that are length (2, 2)
        cache = dtree.treenode.get_cached_content("name")
        edges = [i for i in dtree.treenode.get_edges(cache) if len(i[0]) == 2]
        
        # unresolved subtree
        if not edges:
            arr[3] += 1
            
        # store resolved tree
        else:
            split = [i for i in edges[0] if tips[0] in i][0]
            split.remove(tips[0])
            nidx = tips.index(split.pop())
            print(tips, nidx)

    return arr
    


In [328]:
tre = toytree.tree(tw.tree_weights.loc[2100, "subtree"])
# quart = ['bran-1', 'fusi-n-1', 'fusi-s-0', 'virg-0']
# quart = ['bran-1', 'fusi-n-1', 'fusi-s-1', 'virg-0']
# droptips = set(tre.get_tip_labels()) - set(quart)
# dtre = tre.drop_tips(droptips)
# dtre.draw();

# [dtre.treenode.get_distance(i, topology_only=True) for i in dtre.treenode.get_leaves()]
# dtre.treenode.get_edges(dtre.treenode.get_cached_content("name"))
tre.draw(use_edge_lengths=False);

fusi-n-1 bran-2 bran-1 virg-4 fusi-s-1 bran-0 virg-3 virg-2 fusi-n-0 fusi-s-0 virg-1 virg-0

In [324]:
calculate_weights(tw.imap, toytree.tree(tw.tree_weights.loc[2100, "subtree"]))

['bran-1', 'fusi-n-1', 'fusi-s-0', 'virg-2'] 1
['bran-1', 'fusi-n-1', 'fusi-s-0', 'virg-1'] 1
['bran-1', 'fusi-n-1', 'fusi-s-0', 'virg-0'] 1
['bran-1', 'fusi-n-1', 'fusi-s-0', 'virg-3'] 1
['bran-1', 'fusi-n-0', 'fusi-s-1', 'virg-2'] 2
['bran-1', 'fusi-n-0', 'fusi-s-1', 'virg-1'] 2
['bran-1', 'fusi-n-0', 'fusi-s-1', 'virg-0'] 2
['bran-1', 'fusi-n-0', 'fusi-s-1', 'virg-3'] 2
['bran-1', 'fusi-n-0', 'fusi-s-0', 'virg-4'] 3
['bran-1', 'fusi-n-0', 'fusi-s-0', 'virg-2'] 3
['bran-1', 'fusi-n-0', 'fusi-s-0', 'virg-3'] 3
['bran-2', 'fusi-n-1', 'fusi-s-0', 'virg-2'] 1
['bran-2', 'fusi-n-1', 'fusi-s-0', 'virg-1'] 1
['bran-2', 'fusi-n-1', 'fusi-s-0', 'virg-0'] 1
['bran-2', 'fusi-n-1', 'fusi-s-0', 'virg-3'] 1
['bran-2', 'fusi-n-0', 'fusi-s-1', 'virg-2'] 2
['bran-2', 'fusi-n-0', 'fusi-s-1', 'virg-1'] 2
['bran-2', 'fusi-n-0', 'fusi-s-1', 'virg-0'] 2
['bran-2', 'fusi-n-0', 'fusi-s-1', 'virg-3'] 2
['bran-2', 'fusi-n-0', 'fusi-s-0', 'virg-4'] 3
['bran-2', 'fusi-n-0', 'fusi-s-0', 'virg-2'] 3
['bran-2', 'f

array([ 0,  0,  0, 27])

In [170]:
toytree.tree(tw.tree_weights.loc[2400].subtree).draw();

bran-2 bran-1 bran-0 fusi-s-0 fusi-s-1 fusi-n-1 fusi-n-0 virg-2 virg-1 virg-0 virg-3

In [25]:
tw = weights["scaf-2-vbff"]
tw.tree_weights.head()
tw.wmap

{'abcd': 'bran,fusi-n|fusi-s,virg',
 'acbd': 'bran,fusi-s|fusi-n,virg',
 'adbd': 'bran,virg|fusi-n,fusi-s',
 'unknown': 'unknown'}

In [31]:
df1 = tw.tree_weights.loc[:, ["fabcd", "facbd", "fadbc"]]
#df1 = tw.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc", "uunk"]]
#df1 = tw.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc"]]

fills = df1.rolling(window=10, min_periods=2, win_type="boxcar", center=True).mean()
lines = df1.rolling(window=100, min_periods=2, win_type="boxcar", center=True).mean()

canvas = toyplot.Canvas(width=900, height=250)
axes = canvas.cartesian(
    label="Chromosome ",
    xlabel="Position (Mb)",
    ylabel="Subtree weighting",
)
m = axes.fill(fills, baseline="stacked", opacity=0.4)
m = axes.plot(lines, stroke_width=1.5)

axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=np.arange(0, 3000, 500),
    labels=(tw.tree_table.start[np.arange(0, 3000, 500)] / int(1e6)).astype(int),
)

<polygon points="51.39470013947001,200.0 51.67364016736401,200.0 51.952580195258015,200.0 52.23152022315202,200.0 52.51046025104603,200.0 52.78940027894002,200.0 53.06834030683403,200.0 53.34728033472803,200.0 53.626220362622036,200.0 53.90516039051604,200.0 54.18410041841004,200.0 54.46304044630404,200.0 54.741980474198044,200.0 55.02092050209205,200.0 55.29986052998605,200.0 55.57880055788006,200.0 55.85774058577406,200.0 56.13668061366806,200.0 56.41562064156207,200.0 56.69456066945607,200.0 56.973500697350076,200.0 57.25244072524407,200.0 57.53138075313807,200.0 57.81032078103208,200.0 58.08926080892608,200.0 58.36820083682009,200.0 58.64714086471409,200.0 58.92608089260809,200.0 59.20502092050209,200.0 59.483960948396096,200.0 59.7629009762901,200.0 60.0418410041841,200.0 60.3207810320781,200.0 60.599721059972104,200.0 60.87866108786611,200.0 61.15760111576011,200.0 61.43654114365411,200.0 61.71548117154812,200.0 61.994421199442115,200.0 62.273361227336125,200.0 62.55230125523012,200.0 62.83124128312413,200.0 63.11018131101814,200.0 63.389121338912126,200.0 63.668061366806135,200.0 63.94700139470014,200.0 64.22594142259415,200.0 64.50488145048814,200.0 64.78382147838215,200.0 65.06276150627615,200.0 65.34170153417016,200.0 65.62064156206415,200.0 65.89958158995816,200.0 66.17852161785217,200.0 66.45746164574616,200.0 66.73640167364016,200.0 67.01534170153417,200.0 67.29428172942818,200.0 67.57322175732217,200.0 67.85216178521618,200.0 68.13110181311018,200.0 68.41004184100419,200.0 68.68898186889818,200.0 68.96792189679219,200.0 69.24686192468619,200.0 69.5258019525802,200.0 69.8047419804742,200.0 70.0836820083682,200.0 70.3626220362622,200.0 70.6415620641562,200.0 70.92050209205021,200.0 71.19944211994421,200.0 71.47838214783822,200.0 71.75732217573221,200.0 72.03626220362622,200.0 72.31520223152023,200.0 72.59414225941423,200.0 72.87308228730822,200.0 73.15202231520223,200.0 73.43096234309624,200.0 73.70990237099024,200.0 73.98884239888423,200.0 74.26778242677824,200.0 74.54672245467225,200.0 74.82566248256624,200.0 75.10460251046025,200.0 75.38354253835425,200.0 75.66248256624826,200.0 75.94142259414227,200.0 76.22036262203628,200.0 76.49930264993026,200.0 76.77824267782427,200.0 77.05718270571826,200.0 77.33612273361227,200.0 77.61506276150628,200.0 77.89400278940028,200.0 78.17294281729428,200.0 78.4518828451883,200.0 78.73082287308229,200.0 79.00976290097628,200.0 79.2887029288703,200.0 79.5676429567643,200.0 79.8465829846583,200.0 80.12552301255229,200.0 80.4044630404463,200.0 80.68340306834031,200.0 80.9623430962343,200.0 81.2412831241283,200.0 81.52022315202231,200.0 81.79916317991632,200.0 82.07810320781033,200.0 82.35704323570431,200.0 82.63598326359833,200.0 82.91492329149233,200.0 83.19386331938634,200.0 83.47280334728033,200.0 83.75174337517433,200.0 84.03068340306834,200.0 84.30962343096235,200.0 84.58856345885636,200.0 84.86750348675035,200.0 85.14644351464435,200.0 85.42538354253836,200.0 85.70432357043235,200.0 85.98326359832637,200.0 86.26220362622036,200.0 86.54114365411436,200.0 86.82008368200837,200.0 86.82008368200837,152.1531100478469 86.54114365411436,159.76874003189795 86.26220362622036,163.57655502392342 85.98326359832637,165.86124401913878 85.70432357043235,165.14078027235922 85.42538354253836,162.9778116620222 85.14644351464435,164.08996020426943 84.86750348675035,164.6316887639483 84.58856345885636,164.0305888530707 84.30962343096235,161.75786158034342 84.03068340306834,168.59996684350133 83.75174337517433,171.09996684350133 83.47280334728033,170.66662982611263 83.19386331938634,164.5555187150015 82.91492329149233,160.49568965517244 82.63598326359833,159.3845785440613 82.35704323570431,157.38137341585616 82.07810320781033,154.34816779644365 81.79916317991632,156.44586894586894 81.52022315202231,156.08744600680086 81.2412831241283,150.59837675765098 80.9623430962343,145.4847403940146 80.68340306834031,147.37532479467964 80.4044630404463,155.07373749309232 80.12552301255229,162.21659463594946 7

In [9]:
tw0.draw_tree_weights()

<polygon points="50.0,200.0 50.291120815138285,200.0 50.58224163027656,200.0 50.87336244541485,200.0 51.164483260553126,200.0 51.45560407569141,200.0 51.7467248908297,200.0 52.037845705967975,200.0 52.32896652110626,200.0 52.620087336244545,200.0 52.91120815138283,200.0 53.20232896652111,200.0 53.49344978165939,200.0 53.78457059679768,200.0 54.07569141193595,200.0 54.366812227074234,200.0 54.65793304221252,200.0 54.9490538573508,200.0 55.24017467248908,200.0 55.53129548762736,200.0 55.822416302765646,200.0 56.113537117903924,200.0 56.40465793304221,200.0 56.695778748180494,200.0 56.98689956331877,200.0 57.27802037845706,200.0 57.56914119359534,200.0 57.86026200873363,200.0 58.15138282387191,200.0 58.44250363901019,200.0 58.733624454148476,200.0 59.024745269286754,200.0 59.31586608442504,200.0 59.606986899563324,200.0 59.8981077147016,200.0 60.18922852983989,200.0 60.480349344978166,200.0 60.77147016011645,200.0 61.06259097525473,200.0 61.35371179039301,200.0 61.64483260553129,200.0 61.93595342066958,200.0 62.22707423580786,200.0 62.51819505094615,200.0 62.80931586608443,200.0 63.10043668122271,200.0 63.39155749636099,200.0 63.682678311499274,200.0 63.97379912663755,200.0 64.26491994177584,200.0 64.55604075691411,200.0 64.8471615720524,200.0 65.13828238719069,200.0 65.42940320232896,200.0 65.72052401746726,200.0 66.01164483260553,200.0 66.30276564774381,200.0 66.5938864628821,200.0 66.88500727802037,200.0 67.17612809315867,200.0 67.46724890829694,200.0 67.75836972343522,200.0 68.04949053857351,200.0 68.3406113537118,200.0 68.63173216885008,200.0 68.92285298398835,200.0 69.21397379912663,200.0 69.50509461426492,200.0 69.7962154294032,200.0 70.08733624454149,200.0 70.37845705967976,200.0 70.66957787481805,200.0 70.96069868995633,200.0 71.2518195050946,200.0 71.5429403202329,200.0 71.83406113537117,200.0 72.12518195050946,200.0 72.41630276564774,200.0 72.70742358078603,200.0 72.99854439592431,200.0 73.28966521106258,200.0 73.58078602620088,200.0 73.87190684133915,200.0 74.16302765647744,200.0 74.45414847161572,200.0 74.745269286754,200.0 75.0363901018923,200.0 75.32751091703057,200.0 75.61863173216885,200.0 75.90975254730714,200.0 76.2008733624454,200.0 76.4919941775837,200.0 76.78311499272198,200.0 77.07423580786026,200.0 77.36535662299855,200.0 77.65647743813683,200.0 77.94759825327512,200.0 78.23871906841339,200.0 78.52983988355167,200.0 78.82096069868996,200.0 79.11208151382823,200.0 79.40320232896653,200.0 79.6943231441048,200.0 79.98544395924309,200.0 80.27656477438137,200.0 80.56768558951964,200.0 80.85880640465794,200.0 81.14992721979621,200.0 81.4410480349345,200.0 81.73216885007278,200.0 82.02328966521105,200.0 82.31441048034935,200.0 82.60553129548762,200.0 82.89665211062592,200.0 83.1877729257642,200.0 83.47889374090248,200.0 83.77001455604076,200.0 84.06113537117903,200.0 84.35225618631733,200.0 84.6433770014556,200.0 84.93449781659388,200.0 85.22561863173217,200.0 85.51673944687045,200.0 85.80786026200875,200.0 86.09898107714702,200.0 86.39010189228529,200.0 86.68122270742359,200.0 86.97234352256186,200.0 87.26346433770016,200.0 87.55458515283843,200.0 87.84570596797671,200.0 88.136826783115,200.0 88.42794759825327,200.0 88.71906841339157,200.0 89.01018922852984,200.0 89.30131004366812,200.0 89.59243085880641,200.0 89.88355167394468,200.0 90.17467248908298,200.0 90.46579330422125,200.0 90.75691411935954,200.0 91.04803493449782,200.0 91.33915574963609,200.0 91.63027656477438,200.0 91.92139737991266,200.0 92.21251819505095,200.0 92.50363901018923,200.0 92.79475982532752,200.0 93.0858806404658,200.0 93.37700145560407,200.0 93.66812227074237,200.0 93.95924308588064,200.0 94.25036390101893,200.0 94.5414847161572,200.0 94.83260553129548,200.0 95.12372634643377,200.0 95.41484716157206,200.0 95.70596797671033,200.0 95.99708879184861,200.0 96.2882096069869,200.0 96.57933042212518,200.0 96.87045123726347,200.0 97.16157205240174,200.0 97.45269286754004,200.0 97.74381368267831,200.0 98.03493449781661,200.0 98.32605531295488,200.

### TEST

In [11]:
tw0.wmap

{'abcd': 'bran,mini|oleo,sagr',
 'acbd': 'bran,oleo|mini,sagr',
 'adbd': 'bran,sagr|mini,oleo',
 'unknown': 'unknown'}

In [10]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("bran", "mini", "oleo", "sagr")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# init analysis object
tw0 = ipa.twisst(
    name="sc0-test",
    workdir="../analysis-twisst",
    data="../analysis-treeslider/ts-sc0-wi100000-sl20000.tree_table.csv",
    imap=imap,
    minmap=minmap,
    ipyclient=ipyclient,
)

tw0.run(ipyclient, force=True)
tw0.draw_tree_weights()

[####################] 100% 0:00:59 | calculating tree weights 


<polygon points="50.0,200.0 50.291120815138285,200.0 50.58224163027656,200.0 50.87336244541485,200.0 51.164483260553126,200.0 51.45560407569141,200.0 51.7467248908297,200.0 52.037845705967975,200.0 52.32896652110626,200.0 52.620087336244545,200.0 52.91120815138283,200.0 53.20232896652111,200.0 53.49344978165939,200.0 53.78457059679768,200.0 54.07569141193595,200.0 54.366812227074234,200.0 54.65793304221252,200.0 54.9490538573508,200.0 55.24017467248908,200.0 55.53129548762736,200.0 55.822416302765646,200.0 56.113537117903924,200.0 56.40465793304221,200.0 56.695778748180494,200.0 56.98689956331877,200.0 57.27802037845706,200.0 57.56914119359534,200.0 57.86026200873363,200.0 58.15138282387191,200.0 58.44250363901019,200.0 58.733624454148476,200.0 59.024745269286754,200.0 59.31586608442504,200.0 59.606986899563324,200.0 59.8981077147016,200.0 60.18922852983989,200.0 60.480349344978166,200.0 60.77147016011645,200.0 61.06259097525473,200.0 61.35371179039301,200.0 61.64483260553129,200.0 61.93595342066958,200.0 62.22707423580786,200.0 62.51819505094615,200.0 62.80931586608443,200.0 63.10043668122271,200.0 63.39155749636099,200.0 63.682678311499274,200.0 63.97379912663755,200.0 64.26491994177584,200.0 64.55604075691411,200.0 64.8471615720524,200.0 65.13828238719069,200.0 65.42940320232896,200.0 65.72052401746726,200.0 66.01164483260553,200.0 66.30276564774381,200.0 66.5938864628821,200.0 66.88500727802037,200.0 67.17612809315867,200.0 67.46724890829694,200.0 67.75836972343522,200.0 68.04949053857351,200.0 68.3406113537118,200.0 68.63173216885008,200.0 68.92285298398835,200.0 69.21397379912663,200.0 69.50509461426492,200.0 69.7962154294032,200.0 70.08733624454149,200.0 70.37845705967976,200.0 70.66957787481805,200.0 70.96069868995633,200.0 71.2518195050946,200.0 71.5429403202329,200.0 71.83406113537117,200.0 72.12518195050946,200.0 72.41630276564774,200.0 72.70742358078603,200.0 72.99854439592431,200.0 73.28966521106258,200.0 73.58078602620088,200.0 73.87190684133915,200.0 74.16302765647744,200.0 74.45414847161572,200.0 74.745269286754,200.0 75.0363901018923,200.0 75.32751091703057,200.0 75.61863173216885,200.0 75.90975254730714,200.0 76.2008733624454,200.0 76.4919941775837,200.0 76.78311499272198,200.0 77.07423580786026,200.0 77.36535662299855,200.0 77.65647743813683,200.0 77.94759825327512,200.0 78.23871906841339,200.0 78.52983988355167,200.0 78.82096069868996,200.0 79.11208151382823,200.0 79.40320232896653,200.0 79.6943231441048,200.0 79.98544395924309,200.0 80.27656477438137,200.0 80.56768558951964,200.0 80.85880640465794,200.0 81.14992721979621,200.0 81.4410480349345,200.0 81.73216885007278,200.0 82.02328966521105,200.0 82.31441048034935,200.0 82.60553129548762,200.0 82.89665211062592,200.0 83.1877729257642,200.0 83.47889374090248,200.0 83.77001455604076,200.0 84.06113537117903,200.0 84.35225618631733,200.0 84.6433770014556,200.0 84.93449781659388,200.0 85.22561863173217,200.0 85.51673944687045,200.0 85.80786026200875,200.0 86.09898107714702,200.0 86.39010189228529,200.0 86.68122270742359,200.0 86.97234352256186,200.0 87.26346433770016,200.0 87.55458515283843,200.0 87.84570596797671,200.0 88.136826783115,200.0 88.42794759825327,200.0 88.71906841339157,200.0 89.01018922852984,200.0 89.30131004366812,200.0 89.59243085880641,200.0 89.88355167394468,200.0 90.17467248908298,200.0 90.46579330422125,200.0 90.75691411935954,200.0 91.04803493449782,200.0 91.33915574963609,200.0 91.63027656477438,200.0 91.92139737991266,200.0 92.21251819505095,200.0 92.50363901018923,200.0 92.79475982532752,200.0 93.0858806404658,200.0 93.37700145560407,200.0 93.66812227074237,200.0 93.95924308588064,200.0 94.25036390101893,200.0 94.5414847161572,200.0 94.83260553129548,200.0 95.12372634643377,200.0 95.41484716157206,200.0 95.70596797671033,200.0 95.99708879184861,200.0 96.2882096069869,200.0 96.57933042212518,200.0 96.87045123726347,200.0 97.16157205240174,200.0 97.45269286754004,200.0 97.74381368267831,200.0 98.03493449781661,200.0 98.32605531295488,200.

In [14]:
import toyplot
tw0.draw_tree_weights()

NameError: name 'toyplot' is not defined

In [24]:
df2 = tw0.tree_weights.loc[:, ["fabcd", "facbd", "fadbc"]]

df1 = tw0.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc", "uunk"]]
#df2 = tw0.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc"]]

fills = df2.rolling(window=25, min_periods=1, win_type="boxcar", center=True).mean()
lines = df2.rolling(window=25, min_periods=1, win_type="boxcar", center=True).mean()

canvas = toyplot.Canvas(width=900, height=250)
axes = canvas.cartesian(
    label="Chromosome 2",
    xlabel="Position (Mb)",
    ylabel="Subtree weighting",
)
m = axes.fill(fills, baseline="stacked", opacity=0.4)
m = axes.plot(lines, stroke_width=1.5)

axes.x.ticks.locator = toyplot.locator.Explicit(
    locations=np.arange(0, 3000, 500),
    labels=(tw0.tree_table.start[np.arange(0, 3000, 500)] / int(1e6)).astype(int),
)

In [ ]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("outg", "flor", "oleo", "sagr")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# init analysis object
tw = ipa.twisst(
    name="s2",
    workdir="../analysis-twisst",
    data="./analysis-treeslider/s2.tree_table.csv",
    imap=imap,
    minmap=minmap,
    ipyclient=ipyclient,
)
tw.run(ipyclient)

### Get weights averaged across windows of windows

In [ ]:
df = tw.tree_weights.loc[:, ["fabcd", "facbd", "fadbc"]]
# df = tw.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc", "uunk"]]
aaa = df.rolling(window=20, min_periods=5, win_type="boxcar").mean()
bbb = df.rolling(window=200, min_periods=5, win_type="boxcar").mean()

In [ ]:
canvas = toyplot.Canvas(width=900, height=250)
axes = canvas.cartesian()
m = axes.fill(aaa, baseline="stacked", opacity=0.5)
m = axes.plot(bbb, stroke_width=1.5)

### Test 2

In [6]:
# subsampled dictionary for one hypothesis
imap = {i:j for (i, j) in fullmap.items() if i in ("outg", "mini", "oleo", "sagr")}

# minimum samples in each clade for loci to be included in analysis
minmap = {name: 2 for name in imap}

# init analysis object
tw = ipa.twisst(
    workdir="../analysis-twisst",
    data="./analysis-treeslider/ts-sc0-wi50000-sl10000.tree_table.csv",
    imap=imap,
    minmap=minmap,
    ipyclient=ipyclient,
)
tw.run(ipyclient)

[####################] 100% 0:09:02 | calculating tree weights 

In [50]:
df = tw.tree_weights.loc[:, ["fabcd", "facbd", "fadbc"]]
# df = tw.tree_weights.loc[:, ["uabcd", "uacbd", "uadbc", "uunk"]]
aaa = df.rolling(window=20, min_periods=5, win_type="boxcar").mean()
bbb = df.rolling(window=200, min_periods=5, win_type="boxcar").mean()

In [51]:
canvas = toyplot.Canvas(width=900, height=250)
axes = canvas.cartesian()
m = axes.fill(aaa, baseline="stacked", opacity=0.5)
m = axes.plot(bbb, stroke_width=1.5)

<polygon points="51.2,200.0 51.33333333333333,200.0 51.46666666666666,200.0 51.6,200.0 51.733333333333334,200.0 51.86666666666667,200.0 52.0,200.0 52.13333333333333,200.0 52.266666666666666,200.0 52.4,200.0 52.53333333333333,200.0 52.66666666666667,200.0 52.800000000000004,200.0 52.93333333333333,200.0 53.06666666666666,200.0 53.199999999999996,200.0 53.33333333333333,200.0 53.46666666666666,200.0 53.60000000000001,200.0 53.733333333333334,200.0 53.86666666666667,200.0 54.0,200.0 54.13333333333333,200.0 54.266666666666666,200.0 54.4,200.0 54.53333333333333,200.0 54.666666666666664,200.0 54.800000000000004,200.0 54.93333333333334,200.0 55.06666666666667,200.0 55.2,200.0 55.33333333333333,200.0 55.46666666666667,200.0 55.6,200.0 55.733333333333334,200.0 55.86666666666667,200.0 56.0,200.0 56.13333333333333,200.0 56.266666666666666,200.0 56.4,200.0 56.53333333333333,200.0 56.66666666666667,200.0 56.800000000000004,200.0 56.93333333333333,200.0 57.06666666666666,200.0 57.199999999999996,200.0 57.33333333333333,200.0 57.46666666666667,200.0 57.60000000000001,200.0 57.733333333333334,200.0 57.86666666666667,200.0 58.0,200.0 58.13333333333333,200.0 58.266666666666666,200.0 58.400000000000006,200.0 58.53333333333333,200.0 58.666666666666664,200.0 58.800000000000004,200.0 58.93333333333334,200.0 59.06666666666667,200.0 59.2,200.0 59.33333333333333,200.0 59.46666666666667,200.0 59.6,200.0 59.733333333333334,200.0 59.86666666666667,200.0 60.0,200.0 60.13333333333333,200.0 60.266666666666666,200.0 60.4,200.0 60.53333333333333,200.0 60.66666666666667,200.0 60.800000000000004,200.0 60.93333333333333,200.0 61.06666666666666,200.0 61.199999999999996,200.0 61.33333333333333,200.0 61.46666666666667,200.0 61.60000000000001,200.0 61.733333333333334,200.0 61.86666666666667,200.0 62.0,200.0 62.13333333333333,200.0 62.266666666666666,200.0 62.400000000000006,200.0 62.53333333333333,200.0 62.666666666666664,200.0 62.800000000000004,200.0 62.93333333333334,200.0 63.06666666666667,200.0 63.2,200.0 63.33333333333333,200.0 63.46666666666666,200.0 63.6,200.0 63.733333333333334,200.0 63.86666666666667,200.0 64.0,200.0 64.13333333333334,200.0 64.26666666666667,200.0 64.4,200.0 64.53333333333333,200.0 64.66666666666667,200.0 64.8,200.0 64.93333333333334,200.0 65.06666666666666,200.0 65.19999999999999,200.0 65.33333333333333,200.0 65.46666666666667,200.0 65.6,200.0 65.73333333333333,200.0 65.86666666666667,200.0 66.0,200.0 66.13333333333333,200.0 66.26666666666667,200.0 66.4,200.0 66.53333333333333,200.0 66.66666666666666,200.0 66.8,200.0 66.93333333333334,200.0 67.06666666666666,200.0 67.2,200.0 67.33333333333333,200.0 67.46666666666667,200.0 67.6,200.0 67.73333333333333,200.0 67.86666666666667,200.0 68.0,200.0 68.13333333333334,200.0 68.26666666666667,200.0 68.4,200.0 68.53333333333333,200.0 68.66666666666667,200.0 68.80000000000001,200.0 68.93333333333334,200.0 69.06666666666666,200.0 69.2,200.0 69.33333333333333,200.0 69.46666666666667,200.0 69.6,200.0 69.73333333333333,200.0 69.86666666666666,200.0 70.0,200.0 70.13333333333333,200.0 70.26666666666667,200.0 70.4,200.0 70.53333333333333,200.0 70.66666666666666,200.0 70.8,200.0 70.93333333333334,200.0 71.06666666666666,200.0 71.2,200.0 71.33333333333334,200.0 71.46666666666667,200.0 71.6,200.0 71.73333333333333,200.0 71.86666666666667,200.0 72.0,200.0 72.13333333333333,200.0 72.26666666666667,200.0 72.4,200.0 72.53333333333333,200.0 72.66666666666667,200.0 72.80000000000001,200.0 72.93333333333334,200.0 73.06666666666666,200.0 73.2,200.0 73.33333333333333,200.0 73.46666666666667,200.0 73.6,200.0 73.73333333333333,200.0 73.86666666666667,200.0 74.0,200.0 74.13333333333334,200.0 74.26666666666667,200.0 74.4,200.0 74.53333333333333,200.0 74.66666666666666,200.0 74.8,200.0 74.93333333333334,200.0 75.06666666666666,200.0 75.2,200.0 75.33333333333334,200.0 75.46666666666667,200.0 75.6,200.0 75.73333333333333,200.0 75.86666666666666,200.0 76.0,200.0 76.13333333333333,200.0 76.26666666666667,200.0 76.4,200.0 76.5333

In [56]:
df = tw.tree_weights.loc[:, ["abcd", "acbd", "adbc", "unk"]]
aaa = df.rolling(20, min_periods=5).mean()

In [63]:
canvas = toyplot.Canvas(width=800, height=250)
axes = canvas.cartesian()
m = axes.fill(aaa, baseline="stacked", opacity=0.75)
#m = axes.plot(aaa, stroke_width=1.5)

<polygon points="51.050000000000004,200.0 51.166666666666664,200.0 51.28333333333333,200.0 51.4,200.0 51.516666666666666,200.0 51.63333333333333,200.0 51.75,200.0 51.86666666666667,200.0 51.983333333333334,200.0 52.1,200.0 52.21666666666667,200.0 52.333333333333336,200.0 52.45,200.0 52.56666666666666,200.0 52.68333333333333,200.0 52.8,200.0 52.916666666666664,200.0 53.03333333333333,200.0 53.150000000000006,200.0 53.266666666666666,200.0 53.38333333333333,200.0 53.5,200.0 53.61666666666667,200.0 53.733333333333334,200.0 53.85,200.0 53.96666666666666,200.0 54.08333333333333,200.0 54.2,200.0 54.31666666666667,200.0 54.43333333333334,200.0 54.550000000000004,200.0 54.666666666666664,200.0 54.78333333333333,200.0 54.9,200.0 55.016666666666666,200.0 55.13333333333333,200.0 55.25,200.0 55.36666666666667,200.0 55.483333333333334,200.0 55.6,200.0 55.71666666666667,200.0 55.833333333333336,200.0 55.95,200.0 56.06666666666666,200.0 56.18333333333333,200.0 56.3,200.0 56.416666666666664,200.0 56.53333333333333,200.0 56.650000000000006,200.0 56.766666666666666,200.0 56.88333333333333,200.0 57.0,200.0 57.11666666666667,200.0 57.233333333333334,200.0 57.35,200.0 57.46666666666666,200.0 57.58333333333333,200.0 57.7,200.0 57.81666666666667,200.0 57.93333333333334,200.0 58.050000000000004,200.0 58.166666666666664,200.0 58.28333333333333,200.0 58.4,200.0 58.516666666666666,200.0 58.63333333333333,200.0 58.75,200.0 58.86666666666667,200.0 58.983333333333334,200.0 59.1,200.0 59.21666666666667,200.0 59.333333333333336,200.0 59.45,200.0 59.56666666666666,200.0 59.68333333333333,200.0 59.8,200.0 59.916666666666664,200.0 60.03333333333333,200.0 60.150000000000006,200.0 60.266666666666666,200.0 60.38333333333333,200.0 60.5,200.0 60.61666666666667,200.0 60.733333333333334,200.0 60.85,200.0 60.96666666666666,200.0 61.08333333333333,200.0 61.2,200.0 61.31666666666667,200.0 61.43333333333334,200.0 61.550000000000004,200.0 61.666666666666664,200.0 61.78333333333333,200.0 61.9,200.0 62.016666666666666,200.0 62.13333333333333,200.0 62.25,200.0 62.36666666666667,200.0 62.483333333333334,200.0 62.6,200.0 62.71666666666667,200.0 62.833333333333336,200.0 62.95,200.0 63.06666666666666,200.0 63.18333333333333,200.0 63.3,200.0 63.416666666666664,200.0 63.53333333333333,200.0 63.65,200.0 63.766666666666666,200.0 63.88333333333333,200.0 64.0,200.0 64.11666666666667,200.0 64.23333333333333,200.0 64.35,200.0 64.46666666666667,200.0 64.58333333333333,200.0 64.7,200.0 64.81666666666666,200.0 64.93333333333334,200.0 65.05000000000001,200.0 65.16666666666666,200.0 65.28333333333333,200.0 65.4,200.0 65.51666666666667,200.0 65.63333333333333,200.0 65.75,200.0 65.86666666666667,200.0 65.98333333333333,200.0 66.1,200.0 66.21666666666667,200.0 66.33333333333334,200.0 66.45,200.0 66.56666666666666,200.0 66.68333333333334,200.0 66.8,200.0 66.91666666666666,200.0 67.03333333333333,200.0 67.15,200.0 67.26666666666667,200.0 67.38333333333333,200.0 67.5,200.0 67.61666666666667,200.0 67.73333333333333,200.0 67.85,200.0 67.96666666666667,200.0 68.08333333333333,200.0 68.19999999999999,200.0 68.31666666666666,200.0 68.43333333333334,200.0 68.55000000000001,200.0 68.66666666666667,200.0 68.78333333333333,200.0 68.9,200.0 69.01666666666667,200.0 69.13333333333333,200.0 69.25,200.0 69.36666666666667,200.0 69.48333333333333,200.0 69.6,200.0 69.71666666666667,200.0 69.83333333333334,200.0 69.95,200.0 70.06666666666666,200.0 70.18333333333334,200.0 70.3,200.0 70.41666666666666,200.0 70.53333333333333,200.0 70.65,200.0 70.76666666666667,200.0 70.88333333333333,200.0 71.0,200.0 71.11666666666667,200.0 71.23333333333333,200.0 71.35,200.0 71.46666666666667,200.0 71.58333333333333,200.0 71.69999999999999,200.0 71.81666666666666,200.0 71.93333333333334,200.0 72.05000000000001,200.0 72.16666666666667,200.0 72.28333333333333,200.0 72.4,200.0 72.51666666666667,200.0 72.63333333333333,200.0 72.75,200.0 72.86666666666666,200.0 72.98333333333333,200.0 73.1,200.0 73.21666666666667,200.0 73.33333333333334,2

In [15]:
import numpy

numpy.random.seed(1234)

samples = numpy.linspace(0, 4 * numpy.pi, 100)
frequency = lambda: numpy.random.normal()
phase = lambda: numpy.random.normal()
amplitude = lambda: numpy.random.uniform(0.1, 1)
wave = lambda: numpy.sin(phase() + (frequency() * samples))
signal = lambda: amplitude() * (2 + wave())
heights = numpy.column_stack([signal() for i in range(10)])

canvas = toyplot.Canvas(width=500, height=300)
axes = canvas.cartesian()
m = axes.fill(heights, baseline="stacked")

<polygon points="50.0,250.0 54.0,250.0 58.0,250.0 62.0,250.0 66.0,250.0 70.0,250.0 74.0,250.0 78.0,250.0 82.0,250.0 86.0,250.0 90.0,250.0 94.0,250.0 98.0,250.0 102.0,250.0 106.0,250.0 110.0,250.0 114.0,250.0 118.0,250.0 122.0,250.0 126.0,250.0 130.0,250.0 134.0,250.0 138.0,250.0 142.0,250.0 146.0,250.0 150.0,250.0 154.0,250.0 158.0,250.0 162.0,250.0 166.0,250.0 170.0,250.0 174.0,250.0 178.0,250.0 182.0,250.0 186.0,250.0 190.0,250.0 194.0,250.0 198.0,250.0 202.0,250.0 206.0,250.0 210.0,250.0 214.0,250.0 218.0,250.0 222.0,250.0 226.0,250.0 230.0,250.0 234.0,250.0 238.0,250.0 242.0,250.0 246.0,250.0 250.0,250.0 254.0,250.0 258.0,250.0 262.0,250.0 266.0,250.0 270.0,250.0 274.0,250.0 278.0,250.0 282.0,250.0 286.0,250.0 290.0,250.0 294.0,250.0 298.0,250.0 302.0,250.0 306.0,250.0 310.0,250.0 314.0,250.0 318.0,250.0 322.0,250.0 326.0,250.0 330.0,250.0 334.0,250.0 338.0,250.0 342.0,250.0 346.0,250.0 350.0,250.0 354.0,250.0 358.0,250.0 362.0,250.0 366.0,250.0 370.0,250.0 374.0,250.0 378.0,250.0 382.0,250.0 386.0,250.0 390.0,250.0 394.0,250.0 398.0,250.0 402.0,250.0 406.0,250.0 410.0,250.0 414.0,250.0 418.0,250.0 422.0,250.0 426.0,250.0 430.0,250.0 434.0,250.0 438.0,250.0 442.0,250.0 446.0,250.0 446.0,243.83311486017777 442.0,244.623333535711 438.0,245.16985301332647 434.0,245.4366988600021 430.0,245.4063060511932 426.0,245.0806751817726 422.0,244.48124077764786 418.0,243.64746037639188 414.0,242.63421725010883 410.0,241.50820773529637 406.0,240.34355097231838 402.0,239.21691004168622 398.0,238.2024456464656 394.0,237.36693451270932 390.0,236.76537383731815 386.0,236.43736111884795 382.0,236.4044876674978 378.0,236.66891736547535 374.0,237.21324423028864 370.0,238.00163815680426 366.0,238.982203420046 362.0,240.0903946911991 358.0,241.25326570889015 354.0,242.39427093859976 350.0,243.43830415283688 346.0,244.3166422694849 342.0,244.97146902207518 338.0,245.35968069314285 334.0,245.4557233997409 330.0,245.25327516789167 326.0,244.7656620740763 322.0,244.0249810614096 318.0,243.07998717078632 314.0,241.99288425919056 310.0,240.83523045489247 306.0,239.68322787135975 302.0,238.61270663264114 298.0,237.6941333848095 294.0,236.98797285626617 290.0,236.54070779040362 286.0,236.38177923701784 282.0,236.52164860660432 278.0,236.95110905206224 274.0,237.6418915058403 270.0,238.54852548036376 266.0,239.61133214527428 262.0,240.76035266333315 258.0,241.91995320379692 254.0,243.0138035100435 250.0,243.96990130916205 246.0,244.725311833691 242.0,245.23031047831986 238.0,245.45165590278253 234.0,245.37477813021047 230.0,245.00473761021894 226.0,244.36589211677065 222.0,243.50029340713468 218.0,242.4649191812454 214.0,241.3279225466638 210.0,240.16414586665869 206.0,239.05019429062057 202.0,238.05939324976177 198.0,237.25696183899578 194.0,236.6957197952648 190.0,236.4126106588055 186.0,236.42626997891608 182.0,236.73579863613864 178.0,237.32082202644935 174.0,238.1428312116803 170.0,239.14771775546473 166.0,240.26933539011256 162.0,241.43385406907154 158.0,242.56461980115722 154.0,243.58720036984522 150.0,244.4342848051066 146.0,245.05011410194976 142.0,245.39415153533594 138.0,245.44375097441102 134.0,245.1956475553009 130.0,244.6661725895121 126.0,243.89017856167482 122.0,242.91874497823557 118.0,241.8158160787215 114.0,240.6539917309303 110.0,239.50974857274045 106.0,238.45840596703164 102.0,237.5691681337841 98.0,236.9005688090917 94.0,236.4966182846458 90.0,236.38390644732334 86.0,236.56985251017838 82.0,237.04221664561487 78.0,237.76990566729935 74.0,238.70501972711344 70.0,239.78600530411103 66.0,240.94170694120342 62.0,242.09605102557356 58.0,243.17305330478646 54.0,244.10182052078804 50.0,244.82121693116886" style="fill:rgb(40%,76.1%,64.7%);fill-opacity:1.0;opacity:1.0;stroke:none"> <polygon points="50.0,244.82121693116886 54.0,244.10182052078804 58.0,243.17305330478646 62.0,242.09605102557356 66.0,240.94170694120342 70.0,239.78600530411103 74.0,238.70501972711344 78.0,237.76990566729935 82.0,237.04221664561487 86.0,236.56985251017838 90.0,23

In [14]:
tw.tree_weights

minmap nnodes      abcd      acbd      adbc       unk  \
0      False    NaN       NaN       NaN       NaN       NaN   
1      False    NaN       NaN       NaN       NaN       NaN   
2      False    NaN       NaN       NaN       NaN       NaN   
3      False    NaN       NaN       NaN       NaN       NaN   
4      False    NaN       NaN       NaN       NaN       NaN   
5       True     20  0.291667  0.263889  0.291667  0.152778   
6       True     22  0.402778  0.166667  0.305556  0.125000   
7       True     19  0.055556  0.388889  0.277778  0.277778   
8       True     19  0.263889  0.236111  0.208333  0.291667   
9       True     19  0.263889  0.236111  0.208333  0.291667   
10     False    NaN       NaN       NaN       NaN       NaN   
11     False    NaN       NaN       NaN       NaN       NaN   
12     False    NaN       NaN       NaN       NaN       NaN   
13     False    NaN       NaN       NaN       NaN       NaN   
14     False    NaN       NaN       NaN       NaN       NaN   
15     False    NaN       NaN       NaN       NaN       NaN   
16     False    NaN       NaN       NaN       NaN       NaN   
17     False    NaN       NaN       NaN       NaN       NaN   
18      True     19  0.416667  0.000000  0.250000  0.333333   
19      True     21  0.333333  0.000000  0.250000  0.416667   
20      True     23  0.245833  0.154167  0.325000  0.275000   
21      True     24  0.287500  0.170833  0.295833  0.245833   
22      True     24  0.287500  0.170833  0.295833  0.245833   
23      True     24  0.328125  0.083333  0.187500  0.401042   
24      True     24  0.291667  0.187500  0.250000  0.270833   
25      True     22  0.322917  0.135417  0.437500  0.104167   
26      True     19  0.203125  0.265625  0.265625  0.265625   
27      True     19  0.203125  0.265625  0.265625  0.265625   
28     False    NaN       NaN       NaN       NaN       NaN   
29      True     23  0.562500  0.125000  0.062500  0.250000   
...      ...    ...       ...       ...       ...       ...   
5472    True     20  0.569444  0.111111  0.222222  0.097222   
5473   False    NaN       NaN       NaN       NaN       NaN   
5474    True     22  0.537500  0.025000  0.075000  0.362500   
5475    True     23  0.218750  0.131250  0.300000  0.350000   
5476    True     23  0.218750  0.131250  0.300000  0.350000   
5477    True     23  0.366667  0.166667  0.020833  0.445833   
5478    True     25  0.187500  0.203125  0.240625  0.368750   
5479    True     22  0.140625  0.078125  0.171875  0.609375   
5480    True     22  0.140625  0.078125  0.171875  0.609375   
5481    True     22  0.140625  0.078125  0.171875  0.609375   
5482    True     20  0.000000  0.062500  0.187500  0.750000   
5483    True     20  0.166667  0.000000  0.458333  0.375000   
5484    True     16  0.000000  0.000000  0.000000  1.000000   
5485    True     16  0.000000  0.000000  0.000000  1.000000   
5486    True     16  0.000000  0.000000  0.000000  1.000000   
5487    True     16  0.000000  0.000000  0.000000  1.000000   
5488    True     20  0.145833  0.088542  0.223958  0.541667   
5489   False    NaN       NaN       NaN       NaN       NaN   
5490   False    NaN       NaN       NaN       NaN       NaN   
5491   False    NaN       NaN       NaN       NaN       NaN   
5492   False    NaN       NaN       NaN       NaN       NaN   
5493   False    NaN       NaN       NaN       NaN       NaN   
5494   False    NaN       NaN       NaN       NaN       NaN   
5495   False    NaN       NaN       NaN       NaN       NaN   
5496   False    NaN       NaN       NaN       NaN       NaN   
5497   False    NaN       NaN       NaN       NaN       NaN   
5498   False    NaN       NaN       NaN       NaN       NaN   
5499   False    NaN       NaN       NaN       NaN       NaN   
5500   False    NaN       NaN       NaN       NaN       NaN   
5501   False    NaN       NaN       NaN       NaN       NaN   

                                                subtree  
0                                        

### Plot results

In [13]:
tw.tree_weights.describe()

abcd         acbd         adbc          unk
count  3265.000000  3265.000000  3265.000000  3265.000000
mean      0.212950     0.159018     0.292358     0.335674
std       0.167655     0.131014     0.203830     0.183589
min       0.000000     0.000000     0.000000     0.000000
25%       0.093750     0.062500     0.151042     0.208333
50%       0.187500     0.145833     0.250000     0.316667
75%       0.291667     0.229167     0.390625     0.444444
max       1.000000     1.000000     1.000000     1.000000

In [34]:
tr = toytree.tree(tw.tree_weights.subtree[19])
tr.draw();

oleo-2 oleo-1 fusi-3 fusi-2 sagr-2 oleo-0 fusi-1 virg-3 sagr-1 sagr-0 virg-2 virg-1 fusi-0 virg-0

In [19]:
droptips = set(tr.get_tip_labels()) - set(quarts[0])
ut = tr.drop_tips(droptips)
ut.draw();

oleo-0 sagr-1 fusi-0 virg-0

In [16]:
def generate_samples(tr):
    # all samples of nkeys 
    tips = sorted(tr.get_tip_labels(), key=lambda x: x.rsplit("-", 1)[0])
    gr = itertools.groupby(tips, lambda x: x.rsplit("-", 1)[0])
    return list(itertools.product(*(set(j) for (i, j) in gr)))

quarts = generate_samples(tr)
quarts[:10]

[('fusi-0', 'oleo-0', 'sagr-1', 'virg-0'),
 ('fusi-0', 'oleo-0', 'sagr-1', 'virg-3'),
 ('fusi-0', 'oleo-0', 'sagr-1', 'virg-1'),
 ('fusi-0', 'oleo-0', 'sagr-1', 'virg-2'),
 ('fusi-0', 'oleo-0', 'sagr-2', 'virg-0'),
 ('fusi-0', 'oleo-0', 'sagr-2', 'virg-3'),
 ('fusi-0', 'oleo-0', 'sagr-2', 'virg-1'),
 ('fusi-0', 'oleo-0', 'sagr-2', 'virg-2'),
 ('fusi-0', 'oleo-0', 'sagr-0', 'virg-0'),
 ('fusi-0', 'oleo-0', 'sagr-0', 'virg-3')]

In [22]:
[i.rsplit("-", 1)[0] for i in quarts[0]]
nodes = [tr.treenode&name for name in quarts[0]]
[nodes[0].get_distance]

In [31]:
tn = tr.treenode.search_nodes(name=quarts[0][0])[0]
dists = [tn.get_distance(i, topology_only=True) for i in quarts[0][:]]
order = np.argsort(dists)
np.array([i.name for i in nodes])[order]


array(['fusi-3', 'sagr-2', 'oleo-2', 'virg-3'], dtype='<U6')

In [35]:
for sp in splits:
    print(sp[0].intersection(set(, sp[1])

{'virg-1', 'oleo-0', 'virg-3', 'sagr-1', 'fusi-0', 'fusi-2', 'fusi-3', 'fusi-1', 'oleo-2', 'sagr-2', 'sagr-0', 'oleo-1', 'virg-2'} {'virg-0'}
{'virg-1', 'oleo-0', 'virg-3', 'sagr-1', 'fusi-2', 'fusi-3', 'fusi-1', 'oleo-2', 'sagr-2', 'sagr-0', 'oleo-1', 'virg-2'} {'fusi-0', 'virg-0'}
{'oleo-0', 'virg-3', 'sagr-1', 'fusi-2', 'fusi-3', 'fusi-1', 'oleo-2', 'sagr-2', 'sagr-0', 'oleo-1', 'virg-2'} {'virg-1', 'fusi-0', 'virg-0'}
{'fusi-1', 'virg-3'} {'virg-1', 'oleo-0', 'virg-0', 'sagr-1', 'fusi-0', 'fusi-2', 'fusi-3', 'oleo-1', 'sagr-2', 'sagr-0', 'oleo-2', 'virg-2'}
{'oleo-0', 'fusi-2', 'fusi-3', 'oleo-2', 'sagr-2', 'oleo-1'} {'virg-1', 'virg-2', 'virg-3', 'sagr-1', 'fusi-0', 'fusi-1', 'sagr-0', 'virg-0'}
{'fusi-2', 'fusi-3'} {'virg-1', 'oleo-0', 'virg-3', 'virg-0', 'sagr-1', 'fusi-0', 'fusi-1', 'oleo-1', 'sagr-2', 'sagr-0', 'oleo-2', 'virg-2'}
{'oleo-1', 'oleo-2'} {'virg-1', 'oleo-0', 'virg-3', 'virg-0', 'sagr-1', 'fusi-0', 'fusi-2', 'fusi-3', 'fusi-1', 'sagr-2', 'sagr-0', 'virg-2'}


In [ ]:
def calculate_weight(sample, splits):
    

In [33]:
def get_splits(ttree):
    splits = []
    clade0 = set(tr.get_tip_labels())
    for node in tr.treenode.traverse():
        clade = set(i.name for i in node.get_leaves())
        if len(clade) > 1 and len(clade) < tr.ntips:
            splits.append((clade, clade0 - clade))
    return splits

splits = get_splits(tr)
splits

[({'fusi-0',
   'fusi-1',
   'fusi-2',
   'fusi-3',
   'oleo-0',
   'oleo-1',
   'oleo-2',
   'sagr-0',
   'sagr-1',
   'sagr-2',
   'virg-1',
   'virg-2',
   'virg-3'},
  {'virg-0'}),
 ({'fusi-1',
   'fusi-2',
   'fusi-3',
   'oleo-0',
   'oleo-1',
   'oleo-2',
   'sagr-0',
   'sagr-1',
   'sagr-2',
   'virg-1',
   'virg-2',
   'virg-3'},
  {'fusi-0', 'virg-0'}),
 ({'fusi-1',
   'fusi-2',
   'fusi-3',
   'oleo-0',
   'oleo-1',
   'oleo-2',
   'sagr-0',
   'sagr-1',
   'sagr-2',
   'virg-2',
   'virg-3'},
  {'fusi-0', 'virg-0', 'virg-1'}),
 ({'fusi-1', 'virg-3'},
  {'fusi-0',
   'fusi-2',
   'fusi-3',
   'oleo-0',
   'oleo-1',
   'oleo-2',
   'sagr-0',
   'sagr-1',
   'sagr-2',
   'virg-0',
   'virg-1',
   'virg-2'}),
 ({'fusi-2', 'fusi-3', 'oleo-0', 'oleo-1', 'oleo-2', 'sagr-2'},
  {'fusi-0',
   'fusi-1',
   'sagr-0',
   'sagr-1',
   'virg-0',
   'virg-1',
   'virg-2',
   'virg-3'}),
 ({'fusi-2', 'fusi-3'},
  {'fusi-0',
   'fusi-1',
   'oleo-0',
   'oleo-1',
   'oleo-2',
   'sagr-0',


In [15]:
t = tw.tree_weights.subtree[7]
print(t)

tr = toytree.tree(t)
tr.draw();


((fusi-0:0.010919,virg-0:0.00608304)100:0.00020523,((sagr-0:1e-06,virg-1:1e-06,fusi-1:1e-06,fusi-2:2e-06)100:0.00742816,(oleo-0:1e-06,sagr-1:0.00191418)100:0.0208483,((virg-2:0.00919811,(oleo-2:0.00460369,oleo-3:0.0432686)100:0.00466945)100:0.00479366,oleo-1:0.00642122)100:0.00149609)100:0.0022168);


oleo-3 oleo-2 virg-2 oleo-1 fusi-2 fusi-1 virg-1 sagr-0 sagr-1 oleo-0 virg-0 fusi-0

In [7]:
tw.tree_weights

minmap  weight                                            subtree
0      False     NaN                                                NaN
1      False     NaN                                                NaN
2      False     NaN                                                NaN
3      False     NaN                                                NaN
4      False     NaN                                                NaN
5       True     NaN  (virg-0:0.00626511,sagr-0:1e-06,fusi-0:1e-06,(...
6       True     NaN  ((fusi-0:1e-06,virg-0:0.0056461)100:0.00062437...
7       True     NaN  ((fusi-0:0.010919,virg-0:0.00608304)100:0.0002...
8       True     NaN  (virg-0:0.00640087,(fusi-0:0.0109684,(sagr-0:1...
9       True     NaN  (virg-0:0.00640087,(fusi-0:0.0109684,(sagr-0:1...
10     False     NaN                                                NaN
11     False     NaN                                                NaN
12     False     NaN                                                NaN
13     False     NaN                                                NaN
14     False     NaN                                                NaN
15     False     NaN                                                NaN
16     False     NaN                                                NaN
17     False     NaN                                                NaN
18      True     NaN  ((virg-0:1e-06,(virg-1:1e-06,fusi-1:0.0150263)...
19      True     NaN  (virg-0:0.0023272,(fusi-0:0.00353726,(virg-1:1...
20      True     NaN  (fusi-0:0.00198843,((virg-0:1e-06,virg-1:1e-06...
21      True     NaN  (virg-0:1e-06,(fusi-0:0.00263835,(virg-1:0.002...
22      True     NaN  (virg-0:1e-06,(fusi-0:0.00263835,(virg-1:0.002...
23      True     NaN  (fusi-0:0.00261418,(sagr-0:1e-06,((virg-0:0.00...
24      True     NaN  (fusi-0:0.00321133,(sagr-0:1e-06,(oleo-0:1e-06...
25      True     NaN  (oleo-0:1e-06,(sagr-1:1e-06,(oleo-1:1e-06,(fus...
26      True     NaN  (fusi-0:2e-06,sagr-0:1e-06,fusi-1:1e-06,oleo-0...
27      True     NaN  (fusi-0:2e-06,sagr-0:1e-06,fusi-1:1e-06,oleo-0...
28     False     NaN                                                NaN
29      True     NaN  (sagr-0:1e-06,((fusi-0:1e-06,fusi-2:5e-06)100:...
...      ...     ...                                                ...
5472    True     NaN  ((fusi-0:1e-06,fusi-1:1e-06,(sagr-1:1e-06,virg...
5473   False     NaN                                                NaN
5474    True     NaN  (virg-0:0.00779161,(virg-1:1e-06,(virg-2:1e-06...
5475    True     NaN  ((sagr-0:1e-06,oleo-0:1e-06,(virg-0:1e-06,(ole...
5476    True     NaN  ((sagr-0:1e-06,oleo-0:1e-06,(virg-0:1e-06,(ole...
5477    True     NaN  ((virg-0:1e-06,virg-1:1e-06,virg-2:1e-06)100:0...
5478    True     NaN  ((virg-0:1e-06,virg-1:1e-06)100:0.00281593,(sa...
5479    True     NaN  (fusi-0:1e-06,(sagr-0:1e-06,(((virg-0:0.001208...
5480    True     NaN  (fusi-0:1e-06,(sagr-0:1e-06,(((virg-0:0.001208...
5481    True     NaN  (fusi-0:1e-06,(sagr-0:1e-06,(((virg-0:0.001208...
5482    True     NaN  (fusi-0:1e-06,(sagr-0:1e-06,((fusi-1:1e-06,vir...
5483    True     NaN  (fusi-0:1e-06,(sagr-1:1e-06,virg-0:1e-06,(fusi...
5484    True     NaN  (sagr-0:1e-06,(oleo-1:2e-06,oleo-0:1e-06,fusi-...
5485    True     NaN  (sagr-0:1e-06,(oleo-1:2e-06,oleo-0:1e-06,fusi-...
5486    True     NaN  (sagr-0:1e-06,(oleo-1:2e-06,oleo-0:1e-06,fusi-...
5487    True     NaN  (sagr-0:1e-06,(oleo-1:2e-06,oleo-0:1e-06,fusi-...
5488    True     NaN  (oleo-0:1e-06,(virg-0:2e-06,oleo-1:1e-06,(oleo...
5489   False     NaN                                                NaN
5490   False     NaN                                                NaN
5491   False     NaN                                                NaN
5492   False     NaN                                                NaN
5493   False     NaN                                                NaN
5494   False     NaN                                                NaN
5495   False     NaN                          

In [6]:
minmap

{'virg': 2, 'sagr': 2, 'fusi': 2, 'oleo': 2}

In [7]:
toytree.tree(tree).collapse_polytomies().newick

'(reference:0.0108771,(CRL0030:1e-06,TXGR3:1e-06,MXED8:1e-06)100:0.010908,FLSF47:1e-06,FLSF54:0.0164421,CRL0001:0.00544246,(NI:1e-06,(HE:0.0165408,(AR:1e-06,DO:0.0109302)100:0.0312539)100:0.00715929)100:0.0106932,FLBA140:1e-06,(FLWO6:1e-06,(DU:0.0109765,MXGT4:0.0053917)100:6.6104e-06)100:4.2362e-05);'

In [12]:
dd = toytree.tree(tree).collapse_polytomies().ladderize().draw();

DO AR HE NI MXGT4 DU FLWO6 MXED8 TXGR3 CRL0030 FLBA140 CRL0001 FLSF54 FLSF47 reference

In [10]:

toytree.tree(dd).draw();

DO AR HE NI MXGT4 DU FLWO6 MXED8 TXGR3 CRL0030 FLBA140 CRL0001 FLSF54 FLSF47 reference

In [8]:
toytree.tree(tw.tree_table.tree[0]).draw();

MXGT4 DU FLWO6 FLBA140 DO AR HE NI CRL0001 FLSF54 FLSF47 MXED8 TXGR3 CRL0030 reference

In [36]:
for node in t.treenode.traverse():
    if not node.is_leaf():
        if node.dist <= 1e-6:
            node.delete()
        
t.

22

In [25]:

cache = t.treenode.get_cached_content("name")
splits = [i for i in t.treenode.get_edges(cached_content=cache) if len(i[0]) > 1 and len(i[1]) > 1]
splits

[({'MXED8', 'TXGR3'},
  {'AR',
   'CRL0001',
   'CRL0030',
   'DO',
   'DU',
   'FLBA140',
   'FLSF47',
   'FLSF54',
   'FLWO6',
   'HE',
   'MXGT4',
   'NI',
   'reference'}),
 ({'CRL0030', 'MXED8', 'TXGR3'},
  {'AR',
   'CRL0001',
   'DO',
   'DU',
   'FLBA140',
   'FLSF47',
   'FLSF54',
   'FLWO6',
   'HE',
   'MXGT4',
   'NI',
   'reference'}),
 ({'FLSF47', 'FLSF54'},
  {'AR',
   'CRL0001',
   'CRL0030',
   'DO',
   'DU',
   'FLBA140',
   'FLWO6',
   'HE',
   'MXED8',
   'MXGT4',
   'NI',
   'TXGR3',
   'reference'}),
 ({'AR', 'DO'},
  {'CRL0001',
   'CRL0030',
   'DU',
   'FLBA140',
   'FLSF47',
   'FLSF54',
   'FLWO6',
   'HE',
   'MXED8',
   'MXGT4',
   'NI',
   'TXGR3',
   'reference'}),
 ({'AR', 'DO', 'HE'},
  {'CRL0001',
   'CRL0030',
   'DU',
   'FLBA140',
   'FLSF47',
   'FLSF54',
   'FLWO6',
   'MXED8',
   'MXGT4',
   'NI',
   'TXGR3',
   'reference'}),
 ({'AR', 'DO', 'HE', 'NI'},
  {'CRL0001',
   'CRL0030',
   'DU',
   'FLBA140',
   'FLSF47',
   'FLSF54',
   'FLWO6',
   '

In [32]:
t = toytree.tree(tw.tree_table.tree[0])
clades = []
clade0 = set(i.name for i in ttree.get_leaves())
for node in t.treenode.traverse():#  is_leaf_fn=lambda x: x.dist > 1e-6):
    if node.dist > 1e-6:
        clade = set(i.name for i in node.get_leaves())
        if len(clade) > 1 and len(clade) < t.ntips:
            clades[node.idx] = clade
            print(clade, node.dist)
            print(ttree.get_leaves)
        
#clades

NameError: name 'ttree' is not defined

In [12]:
get_clades(toytree.tree(tw.tree_table.tree[0]))

{26: {'CRL0030', 'MXED8', 'TXGR3'},
 25: {'AR',
  'CRL0001',
  'DO',
  'DU',
  'FLBA140',
  'FLSF47',
  'FLSF54',
  'FLWO6',
  'HE',
  'MXGT4',
  'NI'},
 23: {'FLSF47', 'FLSF54'},
 22: {'AR', 'CRL0001', 'DO', 'DU', 'FLBA140', 'FLWO6', 'HE', 'MXGT4', 'NI'},
 21: {'AR', 'DO', 'DU', 'FLBA140', 'FLWO6', 'HE', 'MXGT4', 'NI'},
 20: {'AR', 'DO', 'HE', 'NI'},
 19: {'DU', 'FLBA140', 'FLWO6', 'MXGT4'},
 17: {'DU', 'FLWO6', 'MXGT4'}}

In [15]:
tw.tree_table.tree[0]

'(reference:0.0108771,(CRL0030:1e-06,(TXGR3:1e-06,MXED8:1e-06)100:1e-06)100:0.010908,((FLSF47:1e-06,FLSF54:0.0164421)100:1e-06,(CRL0001:0.00544246,((NI:1e-06,(HE:0.0165408,(AR:1e-06,DO:0.0109302)100:0.0312539)100:0.00715929)100:0.0106932,(FLBA140:1e-06,(FLWO6:1e-06,(DU:0.0109765,MXGT4:0.0053917)100:6.6104e-06)100:4.2362e-05)100:1e-06)100:1e-06)100:1e-06)100:1e-06);'

In [9]:
def engine_process(newick, rmap, minmap):
    """
    Load toytree for an interval, rename tips to clades with imap, prune
    samples from tree that are not in the test, test for minmap sampling, 
    calculate weights for tree hypothesis, and return tuple of 
    (minmap, weight, subtree).
    """
    # load toytree
    ttree = toytree.tree(newick)
    
    # incremental counter for subtree names from imap
    intmap = {i:0 for i in minmap}

    # keep track of names to drop from tree (not in imap)
    drops = []

    # map names to imap
    for node in ttree.treenode.traverse():
        if node.is_leaf():
            if node.name in rmap:
                imapname = rmap[node.name]
                node.name = "{}-{}".format(imapname, intmap[imapname])
                intmap[imapname] += 1
            else:
                drops.append(node.name)

    # test whether intmap meets minmap filter
    minfilter = [intmap[i] >= minmap[i] for i in minmap]

    # default values
    minmap = False
    weight = np.nan
    subtree = np.nan

    # apply filter
    if not all(minfilter):
        return minmap, weight, subtree
    else:
        # new values
        subtree = ttree.drop_tips(drops).write()
        minmap = True
        return minmap, weight, subtree
        # calculate weight

In [10]:
tw.tree_weights

minmap  weight  subtree
0      False     NaN      NaN
1      False     NaN      NaN
2      False     NaN      NaN
3      False     NaN      NaN
4      False     NaN      NaN
5      False     NaN      NaN
6      False     NaN      NaN
7      False     NaN      NaN
8      False     NaN      NaN
9      False     NaN      NaN
10     False     NaN      NaN
11     False     NaN      NaN
12     False     NaN      NaN
13     False     NaN      NaN
14     False     NaN      NaN
15     False     NaN      NaN
16     False     NaN      NaN
17     False     NaN      NaN
18     False     NaN      NaN
19     False     NaN      NaN
20     False     NaN      NaN
21     False     NaN      NaN
22     False     NaN      NaN
23     False     NaN      NaN
24     False     NaN      NaN
25     False     NaN      NaN
26     False     NaN      NaN
27     False     NaN      NaN
28     False     NaN      NaN
29     False     NaN      NaN
...      ...     ...      ...
5472   False     NaN      NaN
5473   False     NaN      NaN
5474   False     NaN      NaN
5475   False     NaN      NaN
5476   False     NaN      NaN
5477   False     NaN      NaN
5478   False     NaN      NaN
5479   False     NaN      NaN
5480   False     NaN      NaN
5481   False     NaN      NaN
5482   False     NaN      NaN
5483   False     NaN      NaN
5484   False     NaN      NaN
5485   False     NaN      NaN
5486   False     NaN      NaN
5487   False     NaN      NaN
5488   False     NaN      NaN
5489   False     NaN      NaN
5490   False     NaN      NaN
5491   False     NaN      NaN
5492   False     NaN      NaN
5493   False     NaN      NaN
5494   False     NaN      NaN
5495   False     NaN      NaN
5496   False     NaN      NaN
5497   False     NaN      NaN
5498   False     NaN      NaN
5499   False     NaN      NaN
5500   False     NaN      NaN
5501   False     NaN      NaN

[5502 rows x 3 columns]

In [11]:
## how many ways to sample nkeys things from nkeys lists

itertools.combinations()

TypeError: Required argument 'iterable' (pos 1) not found

In [ ]:
list(
    itertools.product(
        iter(set("abcd")), 
        iter(set("efgh")),
        iter(set("ijkl")),
        iter(set("mnop")),
    ), 
)

In [ ]:
tw.tree_weights.head(10)

In [ ]:
toytree.tree(tw.tree_weights.subtree[5]).draw()

In [ ]:
t = toytree.tree(tw.tree_table.tree[9])
toytree.utils.fuzzy_match_tipnames(t, ["AR", "HE"], None, None, False, False)

In [ ]:

def minmap_filter(self):
    
    tree = self.tree_table.tree[15]
    
    
minmap_filter(tw)

In [ ]:
test = tw.tree_table.tree[9]

def map_imap_to_tree(newick):
    # load toytree
    ttree = toytree.tree(newick)
    
    # map names to imap
    intmap = {i:0 for i in tw.imap}
    drops = []
    for node in ttree.treenode.traverse():
        if node.is_leaf():
            if node.name in tw.rmap:
                imapname = tw.rmap[node.name]
                node.name = "{}-{}".format(imapname, intmap[imapname])
                intmap[imapname] += 1
            else:
                drops.append(node.name)
    dtree = ttree.drop_tips(drops)
    return dtree.write(fmt=9)
    
imap_to_tree(test)


In [ ]:


def get_clades(ttree):
    "Used internally by _get_clade_table()"
    clades = {}
    for node in ttree.treenode.traverse():
        clade = set(i.name for i in node.get_leaves())
        if len(clade) > 1 and len(clade) < ttree.ntips:
            clades[node.idx] = clade
    return clades